In [5]:
import pandas as pd
def load_ace_file(filepath):
    with open(filepath, 'r') as file:
        lines = file.readlines()

    # Filter out comment lines
    data_lines = [line for line in lines if not line.startswith(('#', ':')) and line.strip()]
    
    # Convert to a DataFrame using fixed-width format
    from io import StringIO
    data_str = ''.join(data_lines)
    df = pd.read_fwf(StringIO(data_str))
    
    return df

In [ ]:
import numpy as np
import os

def load_ace_file(filepath):
    with open(filepath, 'r') as file:
        lines = file.readlines()

    # Filter out comment lines
    data_lines = [line for line in lines if not line.startswith(('#', ':')) and line.strip()]
    
    # Convert to a DataFrame using fixed-width format
    from io import StringIO
    data_str = ''.join(data_lines)
    df = pd.read_fwf(StringIO(data_str))
    return df

file_path = 'C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily'

file_type = ['epam', 'mag', 'sis', 'swepam']

for year in os.listdir(file_path):
    for type in os.listdir(f'{file_path}/{year}'):
        for types in file_type:

        
            for file in os.listdir(f'{file_path}/{year}/{type}'):
                print(f'{file_path}/{type}/{file}')
            break


C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily/epam/20010807_ace_epam_5m.txt
C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily/epam/20010808_ace_epam_5m.txt
C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily/epam/20010809_ace_epam_5m.txt
C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily/epam/20010810_ace_epam_5m.txt
C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily/epam/20010811_ace_epam_5m.txt
C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily/epam/20010812_ace_epam_5m.txt
C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily/epam/20010813_ace_epam_5m.txt
C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily/epam/20010814_ace_epam_5m.txt
C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily/epam/20010815_ace_epam_5m.txt
C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily/epam/20010816_ace_epam_5m.txt
C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily/epam/20010817_ace_epam_5m.txt
C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily/epam/20010

In [9]:
import numpy as np
import os
import pandas as pd

def load_ace_file(filepath, file_type):
    # Define column names based on file type
    column_mappings = {
        'epam': ['YR', 'MO', 'DA', 'HHMM', 'Julian_Day', 'Seconds_of_Day', 'Electron_S',
                 'Electron_38-53', 'Electron_175-315', 'Proton_S', 'Proton_47-65',
                 'Proton_112-187', 'Proton_310-580', 'Proton_761-1220', 'Proton_1060-1910',
                 'Anisotropy_Ratio'],
        'mag': ['YR', 'MO', 'DA', 'HHMM', 'Julian_Day', 'Seconds_of_Day', 'S',
                'Bx', 'By', 'Bz', 'Bt', 'Latitude', 'Longitude'],
        'sis': ['YR', 'MO', 'DA', 'HHMM', 'Julian_Day', 'Seconds_of_Day', 'S_10MeV',
                'Proton_>10MeV', 'S_30MeV', 'Proton_>30MeV'],
        'swepam': ['YR', 'MO', 'DA', 'HHMM', 'Julian_Day', 'Seconds_of_Day', 'S',
                   'Proton_Density', 'Bulk_Speed', 'Ion_Temperature']
    }
    
    with open(filepath, 'r') as file:
        lines = file.readlines()

    # Filter out comment lines
    data_lines = [line for line in lines if not line.startswith(('#', ':')) and line.strip()]
    
    # Convert to DataFrame using fixed-width format
    from io import StringIO
    data_str = ''.join(data_lines)
    df = pd.read_fwf(StringIO(data_str), names=column_mappings[file_type])
    
    # Handle missing data values
    if file_type in ['epam', 'sis']:
        df = df.replace(-1.00e+05, np.nan)
    elif file_type == 'mag':
        df = df.replace(-999.9, np.nan)
    elif file_type == 'swepam':
        df = df.replace({'Proton_Density': -9999.9, 'Bulk_Speed': -9999.9, 'Ion_Temperature': -1.00e+05}, np.nan)
    
    return df

file_path = 'C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily'
file_types = ['epam', 'mag', 'sis', 'swepam']

# Initialize lists to store metadata
metadata = []

# Create dictionaries to store DataFrames for each file type
dataframes = {
    'epam': [],
    'mag': [],
    'sis': [],
    'swepam': []
}

# Iterate through directory structure
for year in os.listdir(file_path):
    year_path = os.path.join(file_path, year)
    if os.path.isdir(year_path):
        for type_folder in os.listdir(year_path):
            type_path = os.path.join(year_path, type_folder)
            if os.path.isdir(type_path) and type_folder in file_types:
                for file in os.listdir(type_path):
                    if file.endswith('.txt'):
                        file_full_path = os.path.join(type_path, file)
                        # Store metadata
                        metadata.append({
                            'year': year,
                            'type': type_folder,
                            'file_path': file_full_path
                        })
                        # Load and store data
                        try:
                            df = load_ace_file(file_full_path, type_folder)
                            df['year'] = year
                            df['file'] = file
                            dataframes[type_folder].append(df)
                        except Exception as e:
                            print(f"Error processing {file_full_path}: {str(e)}")

# Create metadata DataFrame and save to CSV
metadata_df = pd.DataFrame(metadata)
metadata_df.to_csv('ace_metadata.csv', index=False)
print("Metadata CSV saved as 'ace_metadata.csv'")

# Combine and save DataFrames for each file type
for file_type in file_types:
    if dataframes[file_type]:
        combined_df = pd.concat(dataframes[file_type], ignore_index=True)
        combined_df.to_csv(f'ace_{file_type}_data.csv', index=False)
        print(f"{file_type} data saved as 'ace_{file_type}_data.csv'")
    else:
        print(f"No data found for {file_type}")

KeyboardInterrupt: 

In [13]:
!pip install polars

   ---------------------------------------- 0.0/35.2 MB ? eta -:--:--
   ---------------------------------------- 0.0/35.2 MB 660.6 kB/s eta 0:00:54
   ---------------------------------------- 0.1/35.2 MB 1.3 MB/s eta 0:00:27
   ---------------------------------------- 0.2/35.2 MB 1.6 MB/s eta 0:00:22
   ---------------------------------------- 0.2/35.2 MB 1.7 MB/s eta 0:00:21
    --------------------------------------- 0.5/35.2 MB 2.3 MB/s eta 0:00:16
    --------------------------------------- 0.7/35.2 MB 2.5 MB/s eta 0:00:14
    --------------------------------------- 0.8/35.2 MB 2.8 MB/s eta 0:00:13
   - -------------------------------------- 1.0/35.2 MB 3.0 MB/s eta 0:00:12
   - -------------------------------------- 1.2/35.2 MB 3.1 MB/s eta 0:00:12
   - -------------------------------------- 1.3/35.2 MB 3.1 MB/s eta 0:00:11
   - -------------------------------------- 1.6/35.2 MB 3.3 MB/s eta 0:00:11
   - -------------------------------------- 1.7/35.2 MB 3.4 MB/s eta 0:00:10
   -


[notice] A new release of pip is available: 24.0 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [1]:
import numpy as np
import os
import pandas as pd
import polars as pl
from concurrent.futures import ProcessPoolExecutor
import multiprocessing
from io import StringIO
import logging

# Set up logging to file to avoid console memory issues
logging.basicConfig(
    level=logging.INFO,
    format='%(asctime)s - %(levelname)s - %(message)s',
    handlers=[
        logging.FileHandler('ace_processing.log', mode='w'),
        logging.StreamHandler()  # Optional: keep console output for debugging
    ]
)
logger = logging.getLogger(__name__)

def load_ace_file(filepath, file_type):
    # Define column names based on file type
    column_mappings = {
        'epam': ['YR', 'MO', 'DA', 'HHMM', 'Julian_Day', 'Seconds_of_Day', 'Electron_S',
                 'Electron_38-53', 'Electron_175-315', 'Proton_S', 'Proton_47-65',
                 'Proton_112-187', 'Proton_310-580', 'Proton_761-1220', 'Proton_1060-1910',
                 'Anisotropy_Ratio'],
        'mag': ['YR', 'MO', 'DA', 'HHMM', 'Julian_Day', 'Seconds_of_Day', 'S',
                'Bx', 'By', 'Bz', 'Bt', 'Latitude', 'Longitude'],
        'sis': ['YR', 'MO', 'DA', 'HHMM', 'Julian_Day', 'Seconds_of_Day', 'S_10MeV',
                'Proton_>10MeV', 'S_30MeV', 'Proton_>30MeV'],
        'swepam': ['YR', 'MO', 'DA', 'HHMM', 'Julian_Day', 'Seconds_of_Day', 'S',
                   'Proton_Density', 'Bulk_Speed', 'Ion_Temperature']
    }
    
    try:
        # Read file and filter comment lines
        data_lines = []
        with open(filepath, 'r') as file:
            for line in file:
                if not line.startswith(('#', ':')) and line.strip():
                    data_lines.append(line)
        
        # Use Pandas for parsing fixed-width files, then convert to Polars LazyFrame
        pandas_df = pd.read_fwf(StringIO('\n'.join(data_lines)), names=column_mappings[file_type])
        df = pl.from_pandas(pandas_df).lazy()
        
        # Handle missing data values
        if file_type in ['epam', 'sis']:
            df = df.with_columns(pl.col("*").cast(pl.Float64).replace(-1.00e+05, None))
        elif file_type == 'mag':
            df = df.with_columns(pl.col("*").cast(pl.Float64).replace(-999.9, None))
        elif file_type == 'swepam':
            df = df.with_columns([
                pl.col("Proton_Density").cast(pl.Float64).replace(-9999.9, None),
                pl.col("Bulk_Speed").cast(pl.Float64).replace(-9999.9, None),
                pl.col("Ion_Temperature").cast(pl.Float64).replace(-1.00e+05, None)
            ])
        return df, file_type, os.path.basename(filepath)
    except Exception as e:
        logger.error(f"Error processing {filepath}: {str(e)}")
        return None, file_type, os.path.basename(filepath)

def process_year(year_path, file_types):
    metadata = []
    dataframes = {ft: [] for ft in file_types}
    
    try:
        for type_folder in os.listdir(year_path):
            type_path = os.path.join(year_path, type_folder)
            if os.path.isdir(type_path) and type_folder in file_types:
                for file in os.listdir(type_path):
                    if file.endswith('.txt'):
                        file_full_path = os.path.join(type_path, file)
                        metadata.append({
                            'year': os.path.basename(year_path),
                            'type': type_folder,
                            'file_path': file_full_path
                        })
                        dataframes[type_folder].append((file_full_path, type_folder))
        return metadata, dataframes
    except Exception as e:
        logger.error(f"Error processing year {year_path}: {str(e)}")
        return [], {ft: [] for ft in file_types}

def process_year_wrapper(args):
    """Wrapper function for process_year."""
    year_path, file_types = args
    return process_year(year_path, file_types)

def main():
    file_path = 'C:/Users/harsh/Downloads/aditya-l1-isro-main/ace_daily'
    file_types = ['epam', 'mag', 'sis', 'swepam']
    
    logger.info("Using Polars for DataFrame operations with lazy evaluation")
    
    # Validate file path
    if not os.path.exists(file_path):
        logger.error(f"Directory {file_path} does not exist")
        return
    
    # Collect all metadata and file paths
    all_metadata = []
    all_dataframes = {ft: [] for ft in file_types}
    
    # Process each year directory in parallel
    year_paths = [os.path.join(file_path, year) for year in os.listdir(file_path) if os.path.isdir(os.path.join(file_path, year))]
    
    try:
        with ProcessPoolExecutor(max_workers=min(multiprocessing.cpu_count(), 4)) as executor:
            year_args = [(yp, file_types) for yp in year_paths]
            results = executor.map(process_year_wrapper, year_args)
            
            for metadata, dataframes in results:
                all_metadata.extend(metadata)
                for ft in file_types:
                    all_dataframes[ft].extend(dataframes[ft])
    except Exception as e:
        logger.warning(f"Parallel processing of years failed: {str(e)}. Falling back to sequential processing.")
        for year_path in year_paths:
            metadata, dataframes = process_year(year_path, file_types)
            all_metadata.extend(metadata)
            for ft in file_types:
                all_dataframes[ft].extend(dataframes[ft])
    
    # Process files sequentially and write incrementally to CSV
    for file_type in file_types:
        if all_dataframes[file_type]:
            logger.info(f"Processing files for {file_type}")
            output_file = f'ace_{file_type}_data.csv'
            first_file = True  # Flag to write header only for the first file
            
            for item in all_dataframes[file_type]:
                # Validate tuple structure
                if not isinstance(item, tuple) or len(item) != 2:
                    logger.error(f"Invalid tuple in all_dataframes[{file_type}]: {item}")
                    continue
                filepath, ft = item
                if ft != file_type:
                    logger.error(f"Mismatched file type in {filepath}: expected {file_type}, got {ft}")
                    continue
                
                df, _, filename = load_ace_file(filepath, file_type)
                if df is not None:
                    try:
                        # Add year and file columns
                        year = os.path.basename(os.path.dirname(os.path.dirname(filepath)))
                        df = df.with_columns([
                            pl.lit(year).alias('year'),
                            pl.lit(filename).alias('file')
                        ])
                        # Collect LazyFrame to DataFrame and write to CSV
                        df = df.collect()
                        # Convert to Pandas for CSV writing
                        pandas_df = df.to_pandas()
                        # Write incrementally to CSV
                        pandas_df.to_csv(
                            output_file,
                            mode='a',  # Append mode
                            header=first_file,  # Write header only for first file
                            index=False
                        )
                        first_file = False  # Disable header for subsequent files
                        logger.info(f"Processed and appended {filename} to {output_file}")
                        # Free memory
                        del df
                        del pandas_df
                    except Exception as e:
                        logger.error(f"Error processing {filename} for {file_type}: {str(e)}")
    
    # Save metadata
    try:
        metadata_df = pd.DataFrame(all_metadata)
        if not metadata_df.empty:
            metadata_df.to_csv('ace_metadata.csv', index=False)
            logger.info("Metadata CSV saved as 'ace_metadata.csv'")
        else:
            logger.warning("No metadata collected; metadata CSV not saved")
    except Exception as e:
        logger.error(f"Error saving metadata CSV: {str(e)}")

if __name__ == "__main__":
    main()

2025-07-03 00:20:24,216 - INFO - Using Polars for DataFrame operations with lazy evaluation
Traceback (most recent call last):
  File "c:\Users\harsh\AppData\Local\Programs\Python\Python311\Lib\multiprocessing\queues.py", line 246, in _feed
    send_bytes(obj)
  File "c:\Users\harsh\AppData\Local\Programs\Python\Python311\Lib\multiprocessing\connection.py", line 184, in send_bytes
    self._check_closed()
  File "c:\Users\harsh\AppData\Local\Programs\Python\Python311\Lib\multiprocessing\connection.py", line 137, in _check_closed
    raise OSError("handle is closed")
OSError: handle is closed
2025-07-03 00:20:24,377 - WARNING - Parallel processing of years failed: A process in the process pool was terminated abruptly while the future was running or pending.. Falling back to sequential processing.
2025-07-03 00:20:25,054 - INFO - Processing files for epam
2025-07-03 00:20:25,137 - INFO - Processed and appended 20010807_ace_epam_5m.txt to ace_epam_data.csv
2025-07-03 00:20:25,150 - INFO -